In [22]:
"""
This example loads the pre-trained SentenceTransformer model 'distilroberta-base-paraphrase-v1' from the server.
It then fine-tunes this model for some epochs on the dataset build from DKE standardization terminologies.
Note: In this example, you must specify a SentenceTransformer model.
If you want to fine-tune a huggingface/transformers model like bert-base-uncased, see training_nli.py and training_stsbenchmark.py
"""
from torch.utils.data import DataLoader
import math
from sentence_transformers import SentenceTransformer, LoggingHandler, losses, util, InputExample
from sentence_transformers.evaluation import EmbeddingSimilarityEvaluator
import logging
from datetime import datetime
import os
import gzip
import csv

def train_with_n_samples(n):
    
    #### Just some code to print debug information to stdout
    logging.basicConfig(format='%(asctime)s - %(message)s',
                        datefmt='%Y-%m-%d %H:%M:%S',
                        level=logging.INFO,
                        handlers=[LoggingHandler()])
    #### /print debug information to stdout

    #Check if dataset exsist. If not, download and extract  it
    dataset_path = 'from_all_entries_shuffled.tsv'

    # Read the dataset
    model_name = 'distilroberta-base-paraphrase-v1'
    train_batch_size = 16
    num_epochs = 4
    model_save_path = 'fine-tuned_model/varying_train_size/fixed test set/fine-tuning-'+model_name+'-'+datetime.now().strftime("%Y-%m-%d_%H-%M-%S")
   
    
    train_size = 0
    
    # Load a pre-trained sentence transformer model
    model = SentenceTransformer(model_name)

    # Convert the dataset to a DataLoader ready for training
    logging.info("Read training dataset")

    train_samples = []
    dev_samples = []
    test_samples = []

    with open(dataset_path, 'rt', encoding='utf8') as fIn:
        reader = csv.DictReader(fIn, delimiter='\t', quoting=csv.QUOTE_NONE)
        for row in reader:
            score = float(row['score'])
            inp_example = InputExample(texts=[row['sentence1'], row['sentence2']], label=score)

            if row['split'] == 'dev':
                dev_samples.append(inp_example)
            elif row['split'] == 'test':
                test_samples.append(inp_example)
            else:
                if train_size <= n:
                    train_samples.append(inp_example)
                    train_size = train_size + 1

    train_dataloader = DataLoader(train_samples, shuffle=True, batch_size=train_batch_size)
    train_loss = losses.CosineSimilarityLoss(model=model)


    # Development set: Measure correlation between cosine score and gold labels
    logging.info("Read development dataset")
    evaluator = EmbeddingSimilarityEvaluator.from_input_examples(dev_samples, name='development dataset')


    # Configure the training. We skip evaluation in this example
    warmup_steps = math.ceil(len(train_dataloader) * num_epochs * 0.1) #10% of train data for warm-up
    logging.info("Warmup-steps: {}".format(warmup_steps))


    # Train the model
    model.fit(train_objectives=[(train_dataloader, train_loss)],
              evaluator=evaluator,
              epochs=num_epochs,
              evaluation_steps=1000,
              warmup_steps=warmup_steps,
              output_path=model_save_path)


    ##############################################################################
    #
    # Load the stored model and evaluate its performance on test dataset
    #
    ##############################################################################
    model = SentenceTransformer(model_save_path)
    test_evaluator = EmbeddingSimilarityEvaluator.from_input_examples(test_samples, name='test')
    test_evaluator(model, output_path='fine-tuned_model/fine-tuning-distilroberta-base-paraphrase-v1-2021-05-10_14-17-46')
    
    ##############################################################################
    #
    # Load the base model and evaluate its performance on test dataset
    #
    ##############################################################################
    model = SentenceTransformer('distilroberta-base-paraphrase-v1')
    test_evaluator = EmbeddingSimilarityEvaluator.from_input_examples(test_samples, name='test')
    test_evaluator(model, output_path='fine-tuned_model/fine-tuning-distilroberta-base-paraphrase-v1-2021-05-10_16-28-32')
    
    ##############################################################################
    #
    # Load the stored model and evaluate its performance on harbsafe2 test dataset
    #
    ##############################################################################
    test_samples_harbsafe2 = []

    with open('datasets/gold_dataset.tsv', 'rt', encoding='utf8') as fIn:
        reader = csv.DictReader(fIn, delimiter='\t', quoting=csv.QUOTE_NONE)
        for row in reader:
            if row['score'] == "1":
                score = 1
            elif row['score'] == "A":
                score = 0.8
            elif row['score'] == "B":
                score = 0.6
            elif row['score'] == "C":
                score = 0.4
            else: score = 0

            inp_example = InputExample(texts=[str(row['sentence1']), str(row['sentence2'])], label=score)

            test_samples_harbsafe2.append(inp_example)
            
    model = SentenceTransformer(model_save_path)
    test_evaluator = EmbeddingSimilarityEvaluator.from_input_examples(test_samples_harbsafe2, name='test_harbsafe2')
    test_evaluator(model, output_path='fine-tuned_model/varying_train_size/fine-tuning-distilroberta-base-paraphrase-v1-2021-06-08_22-47-26')
    



In [ ]:
train_size2 = [round((i/10)*136393) for i in range(1,11)]
train_size1 = [round((i/100)*136393) for i in range(1,10)]
train_sizes = train_size1+train_size2

for i in train_sizes:
    train_with_n_samples(i)

In [ ]:
from pandas import read_csv
import matplotlib.ticker as mtick
import pandas

file1 = "plots/Varied train size with fixed test size/fine_tuned_test_acc.csv"
file2 = "plots/Varied train size with fixed test size/fine_tuned_train_acc.csv"
file3 = "plots/Varied train size with fixed test size/base_test_acc.csv"
file4 = "plots/Varied train size with fixed test size/fine_tuned_harbsafe2_test.csv"

col_list = ["cosine_spearman"]
df_fine_test = read_csv(file1, usecols=col_list)
df_fine_train = read_csv(file2, usecols=col_list)
df_base_test = read_csv(file3, usecols=col_list)
df_fine_harsafe2_test = read_csv(file4, usecols=col_list)

df_fine_test.columns = ['FineModel_test(cosine_spearman)']
df_fine_train.columns = ['FineModel_train(cosine_spearman)']
df_base_test.columns = ['BaseModel_test(cosine_spearman)']
df_fine_harsafe2_test.columns = ['FineModel_harbsafe2_test(cos_spear)']


x_axis = []
train_size2 = [i*10 for i in range(1,11)]
train_size1 = [i for i in range(1,10)]
train_sizes = train_size1+train_size2
for i in train_sizes:
    x_axis.append(i)

#ax.xaxis.set_major_formatter(mtick.PercentFormatter(5.0))
df=pandas.concat([df_fine_test, df_fine_train, df_base_test, df_fine_harsafe2_test, pandas.DataFrame(x_axis, columns=['% of training data used'])],axis=1)
#df.to_csv("plots/Varied train size/plot4_values.csv")
ax=df.plot(x='% of training data used', y=['FineModel_test(cosine_spearman)','FineModel_train(cosine_spearman)', 'BaseModel_test(cosine_spearman)', 'FineModel_harbsafe2_test(cos_spear)'])
ax.legend(loc='center left', bbox_to_anchor=(1, 0.5))
fig1 = ax.get_figure()
fig2=df.plot(x='% of training data used', y='FineModel_test(cosine_spearman)').get_figure()
fig3=df.plot(x='% of training data used', y='FineModel_train(cosine_spearman)').get_figure()
fig4=df.plot(x='% of training data used', y='BaseModel_test(cosine_spearman)').get_figure()
fig5=df.plot(x='% of training data used', y='FineModel_harbsafe2_test(cos_spear)').get_figure()

fig1.savefig("plots/Varied train size with fixed test size/compare.jpg",bbox_inches='tight')
fig2.savefig("plots/Varied train size with fixed test size/FineModel_test_acc.jpg",bbox_inches='tight')
fig3.savefig("plots/Varied train size with fixed test size/FineModel_train_acc.jpg",bbox_inches='tight')
fig4.savefig("plots/Varied train size with fixed test size/BaseModel_test_acc.jpg",bbox_inches='tight')
fig5.savefig("plots/Varied train size with fixed test size/FineModel_harbsafe2_test_acc.jpg",bbox_inches='tight')

In [ ]:
##### Creating 

from sentence_transformers import SentenceTransformer, LoggingHandler, losses, util, InputExample
import pandas as pd

#Check if dataset exsist. If not, download and extract  it
dataset_path = 'from_all_entries_shuffled.tsv'

model_name = 'distilroberta-base-paraphrase-v1'

# Load a pre-trained sentence transformer model
model = SentenceTransformer(model_name)


score_SBERT = []
with open(dataset_path, 'rt', encoding='utf8') as fIn:
        reader = csv.DictReader(fIn, delimiter='\t', quoting=csv.QUOTE_NONE)
        for row in reader:        
            #Compute embedding for both lists
            embeddings1 = model.encode(row['sentence1'], convert_to_tensor=True)
            embeddings2 = model.encode(row['sentence2'], convert_to_tensor=True)

            #Compute cosine-similarits
            score_SBERT.append(float(util.pytorch_cos_sim(embeddings1, embeddings2)))

df = pd.read_csv('from_all_entries_shuffled.tsv', delimiter='\t')
new_df=pd.concat([df, pd.DataFrame(score_SBERT, columns=['score_SBERT'])],axis=1)
new_df.to_csv('all_entries_shuffled_with SBERT_score.tsv')

2021-06-15 17:24:47 - Load pretrained SentenceTransformer: distilroberta-base-paraphrase-v1
2021-06-15 17:24:47 - Did not find folder distilroberta-base-paraphrase-v1
2021-06-15 17:24:47 - Search model on server: http://sbert.net/models/distilroberta-base-paraphrase-v1.zip
2021-06-15 17:24:47 - Load SentenceTransformer from folder: C:\Users\localadm/.cache\torch\sentence_transformers\sbert.net_models_distilroberta-base-paraphrase-v1
2021-06-15 17:24:48 - Use pytorch device: cuda


Exception ignored in: <function tqdm.__del__ at 0x00000196361108B0>
Traceback (most recent call last):
  File "C:\Users\localadm\anaconda3\lib\site-packages\tqdm\std.py", line 1122, in __del__
    self.close()
  File "C:\Users\localadm\anaconda3\lib\site-packages\tqdm\notebook.py", line 261, in close
    self.sp(bar_style='danger')
AttributeError: 'tqdm_notebook' object has no attribute 'sp'


IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)

